In [0]:
# Valid credentials
sas_token = "sv=2024-11-04&ss=bfqt&srt=co&sp=rwdlacupyx&se=2025-05-19T15:21:36Z&st=2025-05-05T07:21:36Z&spr=https&sig=25%2FT3LltnjZF2rDlnec%2FQQUA16Q%2BdqxKHcA7%2F4%2FEiFs%3D"  # Replace with SAS token
storage_account = "mayfairproject"
container = "customer-reviews"

dbutils.fs.mount(
  source = f"wasbs://{container}@{storage_account}.blob.core.windows.net/raw/reviews",
  mount_point = "/mnt/reviews",
  extra_configs = {f"fs.azure.sas.{container}.{storage_account}.blob.core.windows.net": sas_token}
)

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-6899646972855683>, line 6
      3 storage_account = "mayfairproject"
      4 container = "customer-reviews"
----> 6 dbutils.fs.mount(
      7   source = f"wasbs://{container}@{storage_account}.blob.core.windows.net/raw/reviews",
      8   mount_point = "/mnt/reviews",
      9   extra_configs = {f"fs.azure.sas.{container}.{storage_account}.blob.core.windows.net": sas_token}
     10 )

File /databricks/python_shell/dbruntime/dbutils.py:364, in DBUtils.FSHandler.prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    362 exc.__context__ = None
    363 exc.__cause__ = None
--> 364 raise exc

ExecutionError: An error occurred while calling o404.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory already mounted: /mnt/reviews; nested exception is: 
	java

In [0]:
# List all mounts
display(dbutils.fs.mounts())

mountPoint source encryptionType /databricks-datasets databricks-datasets /Volumes UnityCatalogVolumes /mnt/reviews wasbs://customer-reviews@mayfairproject.blob.core.windows.net/raw/reviews /databricks/mlflow-tracking databricks/mlflow-tracking /databricks-results databricks-results /databricks/mlflow-registry databricks/mlflow-registry /Volume DbfsReserved /volumes DbfsReserved / DatabricksRoot /volume DbfsReserved

In [0]:
df = spark.read \
    .format("csv") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load("/mnt/reviews/*.csv")


In [0]:
# Show schema and sample data
df.printSchema()
display(df.limit(5))

# Check total rows
print(f"Total reviews: {df.count()}")

root
 |-- review_id: string (nullable = true)
 |-- review _content: string (nullable = true)
 |-- rating: string (nullable = true)
 |-- date: string (nullable = true)
 |-- country: string (nullable = true)



review_id review _content rating date country 6.01E+16 Same to this one as well, very classy and soft, no bad smells. Perfect for my neck too. Vibrant colors 5 2024-11-08 United States 6.01E+16 Beautiful colors, exactly what I wanted, but the item has a defect. 4 2024-10-15 United States 6.01E+16 This is top notch scarf, so soft and classy no smells just perfect for my neck. Colors are vibrant too. 5 2024-11-08 United States 6.01E+16 Item was great; would buy from seller again! 5 2024-11-10 United States 6.01E+16 Nice item 5 2024-10-01 United States

Total reviews: 27247


In [0]:
# Summary statistics for numerical columns
display(df.describe())

# Check for missing values
from pyspark.sql.functions import col, sum

df.select([sum(col(c).isNull().cast("int")).alias(c) for c in df.columns]).show()

summary review_id review _content rating date country count 27245 25085 24530 24980 24335 mean NaN 5.506607929515418E17 8.009036605912085 4.819672131147541 6.22 stddev NaN 2.3462931137045783E19 19.13970656064636 10.130752111933734 15.550231412094709 min Pleased with my purchase." Cable provided works but if you want high end sound you need better connectors (will cost you maybe $10 to $20 on up depending on how high quality connectors you want to get for hoking to this system) I can understand the power adapter all they could do was send a ""change password"" email. I am therefore locked out of my account and cannot delete it or set up a new account with my normal email address. The 30 readings stored on my monitor can be viewed max ðŸ”¸ Requires Batteries â€“ It would be nice if it came with a rechargeable option. 🫀💥 ●Excellent battery life●HD Screen is very nice●Speakers are loud and clear. I mean loud.●Very well built. Took a couple impacts off a concrete wall in Frisbee mode.Some details to be aware of:Amazing tablet. The developers seriously put in the extra time and work. It takes a lot of work to seriously make a tablet this slow. No bloatware, no boatware, this is like an oil tanker fully loaded navigating a square maze.The tablets Wifi would lose to a Gen 1 AOL dial up in a speed competition everytime. The tablet reminds me of a track meet but with all the athletes being mannequins.Wifi range. No range. Drops signal continuously. I have 2 other tablets with zero issues. I mean they have issues but it's more personal .Suggested products with this item:●Food ration●Water●Back up rope for boredom and excessive wait time for loading.The tablet, I think, was inspired by Mobil Ave from the Matrix. Stuck in limbo. the cut at the bottom is not true to the picture. examination of the add will show it recommends size large. I ordered a medium just to be safe but the medium was still to big. but at least it receives the channels I want (which

+---------+---------------+------+----+-------+
|review_id|review _content|rating|date|country|
+---------+---------------+------+----+-------+
|        2|           2162|  2717|2267|   2912|
+---------+---------------+------+----+-------+



In [0]:
# Read CSV files from the mounted directory
df = spark.read \
    .format("csv") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load("/mnt/reviews/*.csv")  # Correct path based on your mount

# Verify the DataFrame exists
display(df.limit(5))

review_id review _content rating date country 6.01E+16 Same to this one as well, very classy and soft, no bad smells. Perfect for my neck too. Vibrant colors 5 2024-11-08 United States 6.01E+16 Beautiful colors, exactly what I wanted, but the item has a defect. 4 2024-10-15 United States 6.01E+16 This is top notch scarf, so soft and classy no smells just perfect for my neck. Colors are vibrant too. 5 2024-11-08 United States 6.01E+16 Item was great; would buy from seller again! 5 2024-11-10 United States 6.01E+16 Nice item 5 2024-10-01 United States

In [0]:
# Clean and Transform the Data

from pyspark.sql.functions import col, to_date, trim

# Rename columns for clarity and ease of use
df_renamed = df.withColumnRenamed("Review ID/author", "review_id") \
              .withColumnRenamed("review _content", "review_text") \
              .withColumnRenamed("Rating", "rating") \
              .withColumnRenamed("Date", "date") \
              .withColumnRenamed("Country", "country")

# Convert "rating" to integer and "date" to date type
df_clean = df_renamed.withColumn("rating", col("rating").cast("int")) \
                    .withColumn("date", to_date(col("date"), "yyyy-MM-dd"))  # Adjust date format if needed

# Trim whitespace from text columns
df_clean = df_clean.withColumn("review_text", trim(col("review_text")))

In [0]:
# Validate the Data

# Check for missing values
from pyspark.sql.functions import when

df_clean.select([
    when(col(c).isNull(), 1).otherwise(0).alias(c)
    for c in df_clean.columns
]).show()

# Summary statistics for ratings
df_clean.describe("rating").show()

+---------+-----------+------+----+-------+
|review_id|review_text|rating|date|country|
+---------+-----------+------+----+-------+
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     1|   1|      1|
|        0|          0|     1|   1|      1|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|   0|      0|
|        0|          0|     0|  

In [0]:
df_clean.write \
    .format("parquet") \
    .mode("overwrite") \
    .save("/mnt/reviews/transformed/cleaned_reviews.parquet")

In [0]:
# Load transformed data from Azure Data Lake
df_clean = spark.read.parquet("/mnt/reviews/transformed/cleaned_reviews.parquet")

# Verify the DataFrame exists
display(df_clean.limit(5))  # Check the first 5 rows

review_id review_text rating date country 6.01E+16 Same to this one as well, very classy and soft, no bad smells. Perfect for my neck too. Vibrant colors 5 2024-11-08 United States 6.01E+16 Beautiful colors, exactly what I wanted, but the item has a defect. 4 2024-10-15 United States 6.01E+16 This is top notch scarf, so soft and classy no smells just perfect for my neck. Colors are vibrant too. 5 2024-11-08 United States 6.01E+16 Item was great; would buy from seller again! 5 2024-11-10 United States 6.01E+16 Nice item 5 2024-10-01 United States

In [0]:
jdbc_url = "jdbc:postgresql://5.tcp.eu.ngrok.io:14205/customerreview"

In [0]:
# JDBC connection parameters
db_table = "customer_review"  # replace with your actual table
db_properties = {
    "user": "postgres",
    "password": "School1.",
    "driver": "org.postgresql.Driver"
}


In [0]:
df = spark.read.jdbc(
    url=jdbc_url,
    table=db_table,
    properties=db_properties
)

df.show()  # Display the first few rows


+--------------+--------------------+------+----------+--------------------+
|     review_id|         review_text|rating|      date|             country|
+--------------+--------------------+------+----------+--------------------+
|R1YWOIQNCIKUI4|The SteelSeries A...|     5|      NULL|      United States |
|R2SV71VFQK2PH7|This keyboard has...|     5|      NULL|      United States |
| RE5Y1Y0D2RL48|I upgraded from m...|     5|      NULL|      United States |
|R1H4QCU8FX0G7O|This is the best ...|     5|      NULL|      United States |
|R2UYFA7YO1GAHN|I came from an ol...|     5|      NULL|      United States |
|R37FTMH2F89N14|So far the keyboa...|     4|      NULL|      United States |
| RF72YD1658LU2|First impression ...|     2|      NULL|     United Kingdom |
|R2CMZNHFH0O3FX|it was nice and w...|     5|      NULL|     United Kingdom |
| RKTI6KNBE6SE3|The stainless ste...|     5|      NULL|     United Kingdom |
|      6.01E+16|           Very nice|     5|2025-01-02|              Mexico|

In [0]:
# Read data from PostgreSQL
df = (spark.read
  .format("jdbc")
  .option("url", "jdbc:postgresql://5.tcp.eu.ngrok.io:14205/customerreview")
  .option("dbtable", "customer_review")  # e.g., "public.reviews"
  .option("user", "postgres")
  .option("password", "School1.")
  .option("driver", "org.postgresql.Driver")
  .load()
)

display(df)

review_id review_text rating date country R1YWOIQNCIKUI4 The SteelSeries Apex Pro TKL HyperMagnetic is hands down one of the best gaming keyboards I've ever used! The build quality is outstanding, with a solid aluminum frame that feels premium and durable. Every keypress is smooth, responsive, and satisfying, whether I'm gaming or typing. The adjustable actuation is a game-changer, allowing me to customize key sensitivity to fit my playstyle perfectly.✅ Pros: Premium Build Quality – The aluminum frame makes it feel solid and high-end. No flex or cheap plastic feel. Smooth & Satisfying Typing – The magnetic switches feel buttery smooth and make both gaming and typing a joy. Adjustable Actuation – Being able to tweak the sensitivity per key is an awesome feature, especially for fast-paced games. Compact & Sleek – The TKL design saves space while still feeling comfortable to use.⚠️ A Small Warning: SteelSeries Software Isn’t the Best – Compared to Razer Chroma, the SteelSeries GG software isn’t as intuitive. I found it more frustrating than helpful, so I just opted not to use it. Thankfully, the keyboard works amazingly right out of the box, even without software tweaks.🔥 Final Thoughts:If you're looking for a high-quality, ultra-responsive gaming keyboard with an amazing feel and top-tier build, this is 100% worth it. The software isn’t as user-friendly as Razer’s, but honestly, the keyboard is so good you don’t even need it. Highly recommend! 💯🔥 5 null United States R2SV71VFQK2PH7 This keyboard has specific sensors for actuation, etc. so you can't really change the sound. The keyboard does sound fine as it is. Excellent quality on the screen and great lighting and colors. I wish you could upload the presets to the keyboard so it always did the same thing instead of needing to connect to the app on startup. Sometimes the keyboard will revert back to default and that sucks. This is a wired keyboard but that doesn't matter to me. Full size because I need the 10 key. 5 null United States RE5Y1Y0D2RL48 I upgraded from my Logitech G915 to this. I am going to say, for me, this was a smart move. This keyboard offers so many functions compared to the G915. I am a gamer, and still am trying to figure out how to use the new things this ketboard has to offer for my gaming (outside of using it to cheat in fps games). I am inpressed with the lighting. My old keyboard had lighting as well, but it was weak. This is much more vibrate and has punch. As well, my old keyboard did not light up secondary key functions. This does. The keyboard lay out fits my hands. The G915 'low profile' just sucked. They didn't offer a wirst rest. This keyboard comes with one. As well I notice with this keyboard, I don't have as many typos like I use to. The keys are pronouced and easy to find without looking at the keyboard. I like the little LED screen in the conrer as well. I have seen people post about it saying it was worthless. Well I can tell you, you can make your own apps for it to your hearts dirsire. Issues: The Steel series program does have issues. Sometimes the lighting shuts off, then right back on. I have notice that the company is pushing out patches and updates. And the issue in not a deal breaker. While this does come with a very nice wrist rest, animal hair tends to stick to it. I have had to buy a lint remover and keep it down stairs with the keyboard. Everytime I pet my cats somehow their hairs sticks to the rest and is a pure pain to get off trying to to it by hand. All in all, it's a expensive keyboard, but this is a case of you ARE getting what you paid for. And Steel Series is doing to Logitech what AMD is doing to Intel: They are making far superior products as far as mouse/keyboard/headset items. 5 null United States R1H4QCU8FX0G7O This is the best keyboard I've ever had. The sound is amazing and the color vibrancy is just a wow. The feel is like no other, the board doesn't feel cheap and rushed but instead polished and clean. The respon

In [0]:

(df_clean.write
  .format("jdbc")
  .option("url", "jdbc:postgresql://5.tcp.eu.ngrok.io:14205/customerreview")
  .option("dbtable", "customer_review")
  .option("user", "postgres")
  .option("password", "School1.")
  .option("driver", "org.postgresql.Driver")
  .mode("overwrite")
  .save()
)

Data Explotatory Analysis

In [0]:
# Basic stats
df_clean.select("rating").describe().show()

# Count of reviews by rating
df_clean.groupBy("rating").count().orderBy("rating").show()

# Reviews by country
df_clean.groupBy("country").count().orderBy("count", ascending=False).show()


+-------+------------------+
|summary|            rating|
+-------+------------------+
|  count|             19588|
|   mean| 8.008627731264038|
| stddev|19.139303521603175|
|    min|                 0|
|    max|               100|
+-------+------------------+

+------+-----+
|rating|count|
+------+-----+
|  NULL| 7659|
|     0|    1|
|     1| 1996|
|     2| 1772|
|     3| 2544|
|     4| 2994|
|     5| 9353|
|    20|   35|
|    40|   18|
|    60|   47|
|    80|  104|
|   100|  724|
+------+-----+

+------------------+-----+
|           country|count|
+------------------+-----+
|   United Kingdom | 8516|
|    United Kingdom| 5800|
|              NULL| 2912|
|     United States| 2370|
|      United State| 1939|
|                US|  405|
|             Spain|  396|
|            Mexico|  229|
|           Ukraine|  229|
|            France|  213|
|            Israel|  202|
|Korea, Republic of|  180|
|            Brazil|  141|
|           Germany|  130|
|            Poland|  129|
|          

Sentiment Analysis on Review Text

In [0]:
!pip install textblob

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 624.3/624.3 kB 12.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 21.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 781.7/781.7 kB 27.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.5/78.5 kB 9.9 MB/s eta 0:00:00

[notice] A new release of pip available: 22.2.2 -> 25.1.1
[notice] To update, run: pip install --upgrade pip


In [0]:
from textblob import TextBlob
from pyspark.sql.functions import udf
from pyspark.sql.types import StringType

def get_sentiment(text):
    try:
        return TextBlob(text).sentiment.polarity
    except:
        return None

sentiment_udf = udf(get_sentiment, StringType())

df_sentiment = df_clean.withColumn("sentiment_score", sentiment_udf(col("review_text")))


In [0]:
from pyspark.sql.functions import when

df_sentiment = df_sentiment.withColumn(
    "sentiment_label",
    when(col("sentiment_score") > 0.1, "Positive")
    .when(col("sentiment_score") < -0.1, "Negative")
    .otherwise("Neutral")
)


In [0]:
df_sentiment.write \
    .format("jdbc") \
    .option("url", jdbc_url) \
    .option("dbtable", "customer_review_enriched") \
    .option("user", "postgres") \
    .option("password", "School1.") \
    .option("driver", "org.postgresql.Driver") \
    .mode("overwrite") \
    .save()
